In [1]:
import pandas as pd
from glob import glob
import ahocorasick
from Bio import pairwise2,SeqIO
from Bio.pairwise2 import format_alignment
from tqdm import tqdm

D:\Pythoncode\venv3.7.9\lib\site-packages\Bio\pairwise2.py:283: BiopythonDeprecationWarning: Bio.pairwise2 has been deprecated, and we intend to remove it in a future release of Biopython. As an alternative, please consider using Bio.Align.PairwiseAligner as a replacement, and contact the Biopython developers if you still need the Bio.pairwise2 module.
  BiopythonDeprecationWarning,


In [2]:
# final_pep_gene_symbol = pd.read_table("/mnt/nfs/wangd/project/paper_db/count/peps_gene_symbol.tsv")
final_pep_gene_symbol = pd.read_table("F:\HPC\paper_db\count\peps_gene_symbol.tsv")

In [3]:
final_pep_gene_symbol

sequence_x     protein_accessions  \
0           AAAAAAAAAPAAAATAATTAATTAATAAQ             GCA_109298   
1                            AAAAPAPPAGPR             GCA_161748   
2        AAAGDLGGDHLAFSCDVAKEHDVQNTFEEMEK              GCA_60405   
3        AAAGDLGGDHLAFSCDVAKEHDVQNTFEEMEK              GCA_60405   
4        AAAGDLGGDHLAFSCDVAKEHDVQNTFEEMEK              GCA_60405   
...                                   ...                    ...   
6203  YWCNDGKNPGAVNACHLSCSALLQDNIADAVACAK             GCA_170013   
6204  YWCNDGKNPGAVNACHLSCSALLQDNIADAVACAK             GCA_170013   
6205  YWCNDGKNPGAVNACHLSCSALLQDNIADAVACAK             GCA_170013   
6206         YWMHFCGGSLIHPQWVLTAAHCLGPDVK  GCA_284206,GCA_284208   
6207                          YYNAKTEDKVR             GCA_154212   

                                            peptidoform gene_symbol  
0                         AAAAAAAAAPAAAATAATTAATTAATAAQ       SRP14  
1                                          AAAAPAPPAGPR        PLK3  
2     AAAGDLGGDHLAFSC[Carbamidomethyl]DVAKEHDVQNTFEEMEK        CBR4  
3     AAAGDLGGDHLAFSC[Carbamidomethyl]DVAKEHDVQ[Deam...        CBR4  
4     AAAGDLGGDHLAFSC[Carbamidomethyl]DVAKEHDVQ[Deam...        CBR4  
...                                                 ...         ...  
6203  YWC[Carbamidomethyl]NDGKN[Deamidated]PGAVNAC[C...         LYZ  
6204  YWC[Carbamidomethyl]NDGKN[Deamidated]PGAVN[Dea...         LYZ  
6205  YWC[Carbamidomethyl]NDGKN[Deamidated]PGAVNAC[C...         LYZ  
6206  YWM[Oxidation]HFC[Carbamidomethyl]GGSLIHPQ[Dea...      TPSAB1  
6207                            YYN[Deamidated]AKTEDKVR       CASP4  

[6208 rows x 4 columns]

In [4]:
len(set(final_pep_gene_symbol["sequence_x"]))

3510

In [5]:
final_pep_gene_symbol_no_gene_symbol = final_pep_gene_symbol[final_pep_gene_symbol["gene_symbol"].isna()]
final_pep_gene_symbol_no_gene_symbol_set = set(final_pep_gene_symbol_no_gene_symbol["sequence_x"])
len(final_pep_gene_symbol_no_gene_symbol_set)

25

In [6]:
all_res_peps = set(final_pep_gene_symbol["sequence_x"])

In [7]:
gene_symbol_proteins = {}
proteins_info = {}
# for record in SeqIO.parse("/mnt/nfs/wangd/project/paper_db/pep_files/save_tmp/Homo_sapiens-GRCh38_all-pep.fa", 'fasta'):
for record in SeqIO.parse("F:\HPC\paper_db\pep_files\save_tmp\Homo_sapiens-GRCh38_all-pep.fa", 'fasta'):
    gene_symbol_list = [x for x in record.description.split(" ") if x.startswith('gene_symbol:')]
    if gene_symbol_list:
        gene_symbol = gene_symbol_list[0].split(':')[-1]
    else:
        continue
    try:
        gene_symbol_proteins[gene_symbol].append(str(record.seq) + ';' + str(record.description))
    except KeyError:
        gene_symbol_proteins[gene_symbol] = [str(record.seq) + ';' + str(record.description)]

    try:
        proteins_info[str(record.seq)].append(str(record.description))
    except KeyError:
        proteins_info[str(record.seq)] = [str(record.description)]

In [8]:
seq_gene_symbol_set = set()
seq_no_gene_symbol_set = set()
for index,row in final_pep_gene_symbol.iterrows():
    try:
        gene_symbols = row["gene_symbol"].split(",")
        for gene_symbol in gene_symbols:
            seq_gene_symbol_set.add(row["sequence_x"] + '+' + gene_symbol)
    except AttributeError:
        seq_no_gene_symbol_set.add(row["sequence_x"])

print("There are {} peptides with no corresponding gene symbol found.".format(len(seq_no_gene_symbol_set)))
for seq in seq_no_gene_symbol_set:
    print(seq)

There are 25 peptides with no corresponding gene symbol found.
NQVVLTMTNMNPVDTATYYCAR
LSCAVSGFTFSSYAMHWVR
ASGYTFTNNGITWVR
NTLYHQMNSLRAEDTAVYYCAR
TGEVVLTQSPGTLSLSPGER
LLIFGASTR
SSPVFQIPKNDNIPEQDSLGLSNLQK
SAGGGTYYADSVK
KTPESFLGPNAALVDLDSLVSRPGPTLPGAK
LEEECEGREPGLETGTQAADCK
TPESFLGPNAALVDLDSLVSRPGPTLPGAK
ASQSISTWLAWYQQKPGK
VLIYGASSLQSGVPSR
ESGPVLVKPTETLTLTCTISGFSLSNAR
ASGYTYTDYYMHWVR
LEEECEGREPGLETGTQAADCKDAPLK
ANGGTTDYAAPVK
SKANGGTTDYAAPVK
LEWMGWINTGNGNTK
DLCPLLSEHGLQCSLEPHLNSNLCVYCCK
NDNIPEQDSLGLSNLQK
YKSDSDNQQGSGVPSR
LSCAASGFTFSTYGMHWVR
AEDTAVYFCAK
DTSISTAYMDLSR


In [9]:
gene_symbol_set = set()
for i in seq_gene_symbol_set:
    if i.split("+")[1]:
        gene_symbol_set.add(i.split("+")[1])

In [10]:
len(gene_symbol_set)

1951

In [16]:
def get_details(start, pep_in_caonical, non_canonical_pep_seq):
    res = []
    i = 0
    j = 0
    for AA1, AA2 in zip(pep_in_caonical, non_canonical_pep_seq):
        i += 1
        j += 1
        if AA1 == AA2:
            continue
        if AA1 == '-' and AA2 != '-':
            # insertion
            res.append(str(start + i) + "-" + ">" + AA2)
            i -= 1
        elif AA2 == '-' and AA1 != '-':
            # deletion
            res.append(str(start + i) + AA1 + ">" + "-")
            j -= 1
        else:
            # substitution
            res.append(str(start + i) + AA1 + ">" + AA2)
    return res

In [17]:
def get_blast_canonical_mismatch1or2_info(pep,prot):
# def get_blast_canonical_mismatch1or2_info(x):
    non_canonical_pep_seq = pep
    # non_canonical_pep_seq = x["peptide"]
    canonical_seq = prot
    # canonical_seq = x["canonical_protein"]

    alignments = pairwise2.align.localms(sequenceA = canonical_seq,sequenceB = non_canonical_pep_seq,match = 1,mismatch = -1,open = -1,extend = -1,one_alignment_only=True)
    alignment = alignments[0]
    start = alignment.start
    end = alignment.end

    res = get_details(start,alignment.seqA[start:end], alignment.seqB[start:end])

    if len(res) == 0:
        score = alignment.score
        mismatch_nums = int(len(non_canonical_pep_seq) - score)
        if mismatch_nums in [1,2]:
            #### left
            res = get_details(start-mismatch_nums,alignment.seqA[start-mismatch_nums:end], alignment.seqB[start-mismatch_nums:end])
            if len(res) in [1,2]:
                return res
            #### right
            else:
                res = get_details(start,alignment.seqA[start:end+mismatch_nums], alignment.seqB[start:end+mismatch_nums])
                return res
        else:
            return ""
    elif len(res) in [1,2]:
        return res
    else:
        return ""

In [18]:
gene_symbol_proteins

{'TRDD1': ['EI;ENSP00000451042.1 pep chromosome:GRCh38:14:22438547:22438554:1 gene:ENSG00000223997.1 transcript:ENST00000415118.1 gene_biotype:TR_D_gene transcript_biotype:TR_D_gene gene_symbol:TRDD1 description:T cell receptor delta diversity 1 [Source:HGNC Symbol;Acc:HGNC:12254]'],
 'TRDD3': ['TGGY;ENSP00000452494.1 pep chromosome:GRCh38:14:22449113:22449125:1 gene:ENSG00000228985.1 transcript:ENST00000448914.1 gene_biotype:TR_D_gene transcript_biotype:TR_D_gene gene_symbol:TRDD3 description:T cell receptor delta diversity 3 [Source:HGNC Symbol;Acc:HGNC:12256]'],
 'TRDD2': ['PSY;ENSP00000451515.1 pep chromosome:GRCh38:14:22439007:22439015:1 gene:ENSG00000237235.2 transcript:ENST00000434970.2 gene_biotype:TR_D_gene transcript_biotype:TR_D_gene gene_symbol:TRDD2 description:T cell receptor delta diversity 2 [Source:HGNC Symbol;Acc:HGNC:12255]'],
 'TRBD1': ['GTGG;ENSP00000488240.1 pep scaffold:GRCh38:HSCHR7_2_CTG6:809186:809197:1 gene:ENSG00000282253.1 transcript:ENST00000631435.1 gene_

In [19]:
blast_infos = dict()
blast_infos_details = dict()
gene_symbol_no_protein_set = set()
for seq_gene_symbol in tqdm(seq_gene_symbol_set):
    pep_seq = seq_gene_symbol.split("+")[0]
    gene_symbol = seq_gene_symbol.split("+")[1]
    if gene_symbol in gene_symbol_proteins.keys():
        for info in gene_symbol_proteins[gene_symbol]:
            prot_seq = info.split(";")[0]
            prot_info = info.split(";")[1]

            alignments_score = pairwise2.align.localms(sequenceA = prot_seq,sequenceB = pep_seq,match = 1,mismatch = -1,open = -1,extend = -1,score_only = True)
            if alignments_score >= len(pep_seq) - 4:
                res = get_blast_canonical_mismatch1or2_info(pep_seq,prot_seq)
                if res:
                    blast_infos_details_key = pep_seq + ";" + prot_seq
                    blast_infos_details[blast_infos_details_key] = res

                    try:
                        blast_infos[seq_gene_symbol].append(info)
                    except KeyError:
                        blast_infos[seq_gene_symbol] = [info]
    else:
        gene_symbol_no_protein_set.add(gene_symbol)
print("There are {} gene_symbols with no corresponding canonical protein sequence found.".format(len(gene_symbol_no_protein_set)))
for gene_symbol in gene_symbol_no_protein_set:
    print(gene_symbol)

100%|██████████| 3537/3537 [43:01<00:00,  1.37it/s]  

There are 14 gene_symbols with no corresponding canonical protein sequence found.
WDR92
srpk1a
DDX58
SKIV2L
UHRF1BP1
FAM160B2
H2BS1
EEF1AKNMT
apol1
Pwp2
FAM207A
FAM160B1
GBA
CBWD2


In [20]:
blast_infos_details

{'GAPMDPNESPAAPEAALPK;MQPWHGKAMQRASEAGATAPKASARNARGAPMDPTESPAAPEAALPKAGKFGPARKSGSRQKKSAPDTQERPPVRATGARAKKAPQRAQDTQPSDATSAPGAEGLEPPAAREPALSRAGSCRQRGARCSTKPRPPPGPWDVPSPGLPVSAPILVRRDAAPGASKLRAVLEKLKLSRDDISTAAGMVKGVVDHLLLRLKCDSAFRGVGLLNTGSYYEHVKISAPNEFDVMFKLEVPRIQLEEYSNTRAYYFVKFKRNPKENPLSQFLEGEILSASKMLSKFRKIIKEEINDIKDTDVIMKRKRGGSPAVTLLISEKISVDITLALESKSSWPASTQEGLRIQNWLSAKVRKQLRLKPFYLVPKHAKEGNGFQEETWRLSFSHIEKEILNNHGKSKTCCENKEEKCCRKDCLKLMKYLLEQLKERFKDKKHLDKFSSYHVKTAFFHRLY': ['35T>N'],
 'GAPMDPNESPAAPEAALPK;MQPWHGKAMQRASEAGATAPKASARNARGAPMDPTESPAAPEAALPKAGKFGPARKSGSRQKKSAPDTQERPPVRATGARAKKAPQRAQDTQPSDATSAPGAEGLEPPAAREPALSRAGSCRQRGARCSTKPRPPPGPWDVPSPGLPVSAPILVRRDAAPGASKLRAVLEKLKLSRDDISTAAGMVKGVVDHLLLRLKCDSAFRGVGLLNTGSYYEHVKISAPNEFDVMFKLEVPRIQLEEYSNTRAYYFVKFKRNPKENPLSQFLEGEILSASKMLSKFRKIIKEEINDIKDTDVIMKRKRGGSPAVTLLISEKISVDITLALESKSSWPASTQEGLRIQNWLSAKVRKQLRLKPFYLVPKHAKEGNGFQEETWRLSFSHIEKEILNNHGKSKTCCENKEEKCCRKDCLKLMKYLLEQLKERFKDKKHLDKFSSYHVKTAFFHVCTQNPQDSQWDRKDLGLCFDNCVTYFLQCLRTEKLENYFIPEFNLFSSNL

In [ ]:
blast_infos = dict()
gene_symbol_no_protein_set = set()
for seq_gene_symbol in tqdm(seq_gene_symbol_set):
    pep_seq = seq_gene_symbol.split("+")[0]
    gene_symbol = seq_gene_symbol.split("+")[1]
    if gene_symbol in gene_symbol_proteins.keys():
        for info in gene_symbol_proteins[gene_symbol]:
            prot_seq = info.split(";")[0]
            prot_info = info.split(";")[1]

            alignments_score = pairwise2.align.localms(sequenceA = prot_seq,sequenceB = pep_seq,match = 1,mismatch = -1,open = -1,extend = -1,score_only = True)
            if alignments_score >= len(pep_seq) - 4:
                try:
                    blast_infos[seq_gene_symbol].append(info)
                except KeyError:
                    blast_infos[seq_gene_symbol] = [info]
    else:
        gene_symbol_no_protein_set.add(gene_symbol)
print("There are {} gene_symbols with no corresponding canonical protein sequence found.".format(len(gene_symbol_no_protein_set)))
for gene_symbol in gene_symbol_no_protein_set:
    print(gene_symbol)

#### Peptide + gene_symbol + protein

In [61]:
peptide_gene_symbol_protein = dict()
for key, value in blast_infos.items():
    prot_set = set()

    pep_seq = key.split("+")[0]
    gene_symbol = key.split("+")[1]

    for info in value:
        prot_set.add(info.split(";")[0])

    if peptide_gene_symbol_protein.get(pep_seq):
        peptide_gene_symbol_protein[pep_seq][gene_symbol] = prot_set
    else:
        peptide_gene_symbol_protein[pep_seq] = {gene_symbol:prot_set}

In [62]:
df = pd.DataFrame([(peptide, gene_symbol, ",".join(protein)) for peptide, inner_dict in peptide_gene_symbol_protein.items() for gene_symbol, protein in inner_dict.items()],
                  columns=['peptide', 'gene_symbol', 'protein'])
# df.to_csv("/mnt/nfs/wangd/project/paper_db/count/blast_canonical_count/peptide_gene_symbol_protein.tsv", header=1, sep="\t", index = None)
df.to_csv(r"F:\HPC\paper_db\count\blast_canonical_count\peptide_gene_symbol_protein.tsv", header=1, sep="\t", index = None)

In [63]:
df

peptide gene_symbol  \
0               GAPMDPNESPAAPEAALPK        CGAS   
1                   SQNKEDYDGLKEEFR       GSTO1   
2             CVDGHCVCNPGFTGEDCGSRR        TNXB   
3                 DGDIHQGFQSLLSEVNR    SERPINB8   
4                WLKDEELSPREPVLPPQK      NDUFB6   
...                             ...         ...   
3421  SPISTGQPTNQSMDDTREDIYVNYPTFSR       CD226   
3422       VPEPDYTKVPEPGSIKVPDQGFIK       SPRR3   
3423      VEQIAAIAQELNELDYHNAVNVNDR       ACTN2   
3424         ELYIPLGESEVAGGASHSSGQR        SYNM   
3425                   LQWFQNHLDPPK       TMA16   

                                                protein  
0     MQPWHGKAMQRASEAGATAPKASARNARGAPMDPTESPAAPEAALP...  
1     MRFCPFAERTRLVLKAKGIRHEVININLKNKPEWFFKKNPFGLVPV...  
2     MMPAQYALTSSLVLLVLLSTARAGPFSSRSNVTLPAPRPPPQPGGH...  
3     MDDLCEANGTFAISLFKILGEEDNSRNVFFSPMSISSALAMVFMGA...  
4     MTGYTPDEKLRLQQLRELRRRWLKDQELSPREPVLPPQKMGPMEKF...  
...                                                 ...  
3421  MDYPTLLLALLHVYRALCEEVLWHTSVPFAENMSLECVYPSMGILT...  
3422  MSSYQQKQTFTPPPQLQQQQVKQPSQPPPQEIFVPTTKEPCHSKVP...  
3423  MNQIEPGVQYNYVYDEDEYMIQEEEWDRDLLLDPAWEKQQRKTFTA...  
3424  MADWLRDYQDLLQVKTGLSLEVATYRALLEGESNPEIVIWAEHVEN...  
3425  MPKAPKGKSAGREKKVIHPYSRKAAQITREAHKQEKKEKLKNEKAL...  

[3426 rows x 3 columns]

In [64]:
df["canonical_protein_seq"] = df["protein"].apply(lambda x : x.split(","))
df = df.explode("canonical_protein_seq", ignore_index=True)
df = df.drop("protein", axis=1)

In [65]:
def get_blast_infos_details(x):
    return blast_infos_details[x["peptide"] + ";" + x["canonical_protein_seq"]]

df["mismatch_info"] = df.apply(lambda x: get_blast_infos_details(x), axis=1)
df["number_mismatches"] = df.apply(lambda x: len(x["mismatch_info"]), axis=1)
df["mismatch_info"] = df.apply(lambda x: ",".join(x["mismatch_info"]), axis=1)

In [66]:
def get_protein_infos(canonical_protein_seq):
    canonical_protein_IDs = set()
    canonical_transcript_IDs = set()
    for info in proteins_info[canonical_protein_seq]:
        canonical_protein_IDs.add(info.split(" ")[0])
        canonical_transcript_IDs.add([x for x in info.split(" ") if x.startswith('transcript:')][0].split(':')[-1])
    return [",".join(canonical_protein_IDs), ",".join(canonical_transcript_IDs)]
df["canonical_protein_ID"] = df.apply(lambda x: get_protein_infos(x["canonical_protein_seq"])[0], axis=1)
df["canonical_transcript_ID"] = df.apply(lambda x: get_protein_infos(x["canonical_protein_seq"])[1], axis=1)

In [67]:
df

peptide gene_symbol  \
0      GAPMDPNESPAAPEAALPK        CGAS   
1      GAPMDPNESPAAPEAALPK        CGAS   
2      GAPMDPNESPAAPEAALPK        CGAS   
3          SQNKEDYDGLKEEFR       GSTO1   
4          SQNKEDYDGLKEEFR       GSTO1   
...                    ...         ...   
11569         LQWFQNHLDPPK       TMA16   
11570         LQWFQNHLDPPK       TMA16   
11571         LQWFQNHLDPPK       TMA16   
11572         LQWFQNHLDPPK       TMA16   
11573         LQWFQNHLDPPK       TMA16   

                                   canonical_protein_seq mismatch_info  \
0      MQPWHGKAMQRASEAGATAPKASARNARGAPMDPTESPAAPEAALP...         35T>N   
1      MQPWHGKAMQRASEAGATAPKASARNARGAPMDPTESPAAPEAALP...         35T>N   
2      MQPWHGKAMQRASEAGATAPKASARNARGAPMDPTESPAAPEAALP...         35T>N   
3      MRFCPFAERTRLVLKAKGIRHEVININLKNKPEWFFKKNPFGLVPV...        112A>D   
4      MRFCPFAERTRLVLKAKGIRHEVININLKNKPEWFFKKNPFGLVPV...        112A>D   
...                                                  ...           ...   
11569  MPKAPKGKSAGREKKVIHPYSRKAAQITREAHKQEKKEKLKNEKAL...   53E>-,54K>-   
11570  MPKAPKGKSAGREKKVIHPYSRKAAQITREAHKQEKKEKLKNEKAL...   53E>-,54K>-   
11571  MPKAPKGKSAGREKKVIHPYSRKAAQITREAHKQEKKEKLKNEKAL...   53E>-,54K>-   
11572  MPKAPKGKSAGREKKVIHPYSRKAAQITREAHKQEKKEKLKNEKAL...   53E>-,54K>-   
11573  XGRKRVASPPGLQSPASHSAPGRVQPPAASSLPPLPASTQPKAPKG...   92E>-,93K>-   

       number_mismatches canonical_protein_ID canonical_transcript_ID  
0                      1    ENSP00000506638.1       ENST00000680833.1  
1                      1    ENSP00000359342.1       ENST00000370318.5  
2                      1    ENSP00000359339.3       ENST00000370315.4  
3                      1    ENSP00000406708.1       ENST00000445155.5  
4                      1    ENSP00000441488.1       ENST00000539281.5  
...                  ...                  ...                     ...  
11569                  2    ENSP00000351380.5      ENST00000358572.10  
11570                  2    ENSP00000426933.1       ENST00000513272.5  
11571                  2    ENSP00000423901.1       ENST00000513134.5  
11572                  2    ENSP00000423375.1       ENST00000508268.1  
11573                  2    ENSP00000425347.1       ENST00000509657.5  

[11574 rows x 7 columns]

In [68]:
df.to_csv(r"F:\HPC\paper_db\count\blast_canonical_count\peptide_gene_symbol_protein_matching_info.tsv", header=1, sep="\t", index = None)

#### Protein + gene_symbol + peptide

In [69]:
protein_gene_symbol_peptide = dict()
for key, value in blast_infos.items():
    pep_seq = key.split("+")[0]
    gene_symbol = key.split("+")[1]
    
    for info in value:
        prot_seq = info.split(";")[0]
        
        if protein_gene_symbol_peptide.get(prot_seq):
            if protein_gene_symbol_peptide.get(prot_seq).get(gene_symbol):
                protein_gene_symbol_peptide[prot_seq][gene_symbol].add(pep_seq)
            else:
                protein_gene_symbol_peptide[prot_seq][gene_symbol] = {pep_seq}
        else:
            protein_gene_symbol_peptide[prot_seq] = {gene_symbol:{pep_seq}} 

In [71]:
df = pd.DataFrame([(protein, gene_symbol, ",".join(peptide)) for protein, inner_dict in protein_gene_symbol_peptide.items() for gene_symbol, peptide in inner_dict.items()], 
                  columns=['protein', 'gene_symbol', 'peptide'])
# df.to_csv("/mnt/nfs/wangd/project/paper_db/count/blast_canonical_count/protein_gene_symbol_peptide.tsv", header=1, sep="\t", index = None)
df.to_csv(r"F:\HPC\paper_db\count\blast_canonical_count\protein_gene_symbol_peptide.tsv", header=1, sep="\t", index = None)

In [72]:
df

protein gene_symbol  \
0     MQPWHGKAMQRASEAGATAPKASARNARGAPMDPTESPAAPEAALP...        CGAS   
1     MQPWHGKAMQRASEAGATAPKASARNARGAPMDPTESPAAPEAALP...        CGAS   
2     MQPWHGKAMQRASEAGATAPKASARNARGAPMDPTESPAAPEAALP...        CGAS   
3     MSGESARSLGKGSAPPGPVPEGSIRIYSMRFCPFAERTRLVLKAKG...       GSTO1   
4     MRFCPFAERTRLVLKAKGIRHEVININLKNKPEWFFKKNPFGLVPV...       GSTO1   
...                                                 ...         ...   
6489  XGRKRVASPPGLQSPASHSAPGRVQPPAASSLPPLPASTQPKAPKG...       TMA16   
6490  MPKAPKGKSAGREKKVIHPYSRKAAQITREAHKQEKKEKLKNEKAL...       TMA16   
6491  MPKAPKGKSAGREKKVIHPYSRKAAQITREAHKQEKKEKLKNEKAL...       TMA16   
6492  MPKAPKGKSAGREKKVIHPYSRKAAQITREAHKQEKKEKLKNEKAL...       TMA16   
6493  MPKAPKGKSAGREKKVIHPYSRKAAQITREAHKQEKKEKLKNEKAL...       TMA16   

                                                peptide  
0                 GAPMDPNESPAAPEAALPK,ENHLSQFLEGEILSASK  
1                 GAPMDPNESPAAPEAALPK,ENHLSQFLEGEILSASK  
2                 GAPMDPNESPAAPEAALPK,ENHLSQFLEGEILSASK  
3     EDYDGLKEEFR,EDYDGLKEEFRK,SQNKEDYDGLK,LEVLTNKK,...  
4     EDYDGLKEEFR,EDYDGLKEEFRK,SQNKEDYDGLK,LEVLTNKK,...  
...                                                 ...  
6489                                       LQWFQNHLDPPK  
6490                                       LQWFQNHLDPPK  
6491                                       LQWFQNHLDPPK  
6492                                       LQWFQNHLDPPK  
6493                                       LQWFQNHLDPPK  

[6494 rows x 3 columns]

#### Gene_symbol + peptide + protein

In [73]:
gene_symbol_peptide_protein = dict()
for key, value in blast_infos.items():
    prot_set = set()
    
    pep_seq = key.split("+")[0]
    gene_symbol = key.split("+")[1]
    
    for info in value:
        prot_set.add(info.split(";")[0])

    if gene_symbol_peptide_protein.get(gene_symbol):
        gene_symbol_peptide_protein[gene_symbol][pep_seq] = prot_set
    else:
        gene_symbol_peptide_protein[gene_symbol] = {pep_seq:prot_set}

In [74]:
gene_symbol_peptide = dict()
gene_symbol_protein = dict()
for gene_symbol,value in gene_symbol_peptide_protein.items():
    for peptide,protein in value.items():
        if gene_symbol_peptide.get(gene_symbol):
            gene_symbol_peptide[gene_symbol].add(peptide)
        else:
            gene_symbol_peptide[gene_symbol] = {peptide}
        
        if gene_symbol_protein.get(gene_symbol):
            gene_symbol_protein[gene_symbol].union(protein)
        else:
            gene_symbol_protein[gene_symbol] = protein
            
gene_symbol_peptide_str = {key: ','.join(value) for key, value in gene_symbol_peptide.items()}
gene_symbol_protein_str = {key: ','.join(value) for key, value in gene_symbol_protein.items()}

In [75]:
df = pd.DataFrame({'gene_symbol': list(gene_symbol_peptide.keys()),
                   'peptide': list(gene_symbol_peptide_str.values()),
                   'protein': list(gene_symbol_protein_str.values())})
# df.to_csv("/mnt/nfs/wangd/project/paper_db/count/blast_canonical_count/gene_symbol_peptide_protein.tsv", header=1, sep="\t", index = None)
df.to_csv(r"F:\HPC\paper_db\count\blast_canonical_count\gene_symbol_peptide_protein.tsv", header=1, sep="\t", index = None)

In [76]:
df

gene_symbol                                            peptide  \
0           CGAS              GAPMDPNESPAAPEAALPK,ENHLSQFLEGEILSASK   
1          GSTO1  EDYDGLKEEFR,EDYDGLKEEFRK,SQNKEDYDGLK,LEVLTNKK,...   
2           TNXB  CVDGHCVCNPGFTGEDCGSRR,LGQMTVRDITSDSLSLSWTVPEGQ...   
3       SERPINB8                                  DGDIHQGFQSLLSEVNR   
4         NDUFB6                                 WLKDEELSPREPVLPPQK   
...          ...                                                ...   
1902        GLCE                           WDYHTTHINQLQLLSTIDESPIFK   
1903      UGT2A1             AFITHGGTNGIYEAIYHGVPMVGIPIFADQPDNIAHMK   
1904       EPRS1                             LKTEKAPQDQVDIAVQELLQLK   
1905       CD226                      SPISTGQPTNQSMDDTREDIYVNYPTFSR   
1906       TMA16                                       LQWFQNHLDPPK   

                                                protein  
0     MQPWHGKAMQRASEAGATAPKASARNARGAPMDPTESPAAPEAALP...  
1     MRFCPFAERTRLVLKAKGIRHEVININLKNKPEWFFKKNPFGLVPV...  
2     MMPAQYALTSSLVLLVLLSTARAGPFSSRSNVTLPAPRPPPQPGGH...  
3     MDDLCEANGTFAISLFKILGEEDNSRNVFFSPMSISSALAMVFMGA...  
4     MTGYTPDEKLRLQQLRELRRRWLKDQELSPREPVLPPQKMGPMEKF...  
...                                                 ...  
1902  MNHVAKQQSEEAFPQEQQKAPPVVGGFNSNVGSKVLGLKYEEIDCL...  
1903  MLNNLLLFSLQISLIGTTLGGNVLIWPMEGSHWLNVKIIIDELIKK...  
1904  MATLSLTVNSGDPPLGALLAVEHVKDDVSISVEEGKENILHVSENV...  
1905  MDYPTLLLALLHVYRALCEEVLWHTSVPFAENMSLECVYPSMGILT...  
1906  MPKAPKGKSAGREKKVIHPYSRKAAQITREAHKQEKKEKLKNEKAL...  

[1907 rows x 3 columns]

#### All 1-2 mismatch_nums Peptides Info Count

In [77]:
all_peptide = set()
all_gene_symbol = set()
all_protein = set()
all_transcript = set()
for key, value in blast_infos.items(): 
    pep_seq = key.split("+")[0]
    all_peptide.add(pep_seq)
    
    gene_symbol = key.split("+")[1]
    all_gene_symbol.add(gene_symbol)
    
    for info in value:
        all_protein.add(info.split(";")[0])
        all_transcript.add([x for x in info.split(" ") if x.startswith('transcript:')][0].split(':')[-1])

In [78]:
print("Number of peptides: {}".format(len(all_peptide)))
print("Number of gene_symbols: {}".format(len(all_gene_symbol)))
print("Number of transcript ids: {}".format(len(all_transcript)))
print("Number of protein seqs: {}".format(len(all_protein)))

Number of peptides: 3386
Number of gene_symbols: 1907
Number of transcript ids: 8329
Number of protein seqs: 6491


### Novel Peptides

In [79]:
fail_peps = all_res_peps - all_peptide

In [80]:
len(fail_peps)

124

In [81]:
df_fail_peps = final_pep_gene_symbol[final_pep_gene_symbol["sequence_x"].isin(fail_peps)]
df_fail_peps

sequence_x protein_accessions  \
27          AAGFEEIEQDLTQRFEEK         GCA_170981   
37            AAPQNGGSSEPPAAPR         GCA_277796   
38            AAPQNGGSSEPPAAPR         GCA_277796   
118                AEDMALYYCAK         GCA_264940   
123                AEDTAVYFCAK         GCA_294782   
...                        ...                ...   
6088           YFSTSVSWPGRGEPR          GCA_61687   
6122  YIQQQKQQQQQQQQQQQQQQQQQR         GCA_231481   
6127          YKSDSDNQQGSGVPSR         GCA_310162   
6128          YKSDSDNQQGSGVPSR         GCA_310162   
6129          YKSDSDNQQGSGVPSR         GCA_310162   

                                  peptidoform gene_symbol  
27                         AAGFEEIEQDLTQRFEEK       DDX58  
37                           AAPQNGGSSEPPAAPR       ZFPM1  
38               AAPQ[Deamidated]NGGSSEPPAAPR       ZFPM1  
118   AEDM[Oxidation]ALYYC[Carbamidomethyl]AK   IGHV3-64D  
123              AEDTAVYFC[Carbamidomethyl]AK         NaN  
...                                       ...         ...  
6088                          YFSTSVSWPGRGEPR       HLA-C  
6122     YIQQQKQQQQQQQQQ[Deamidated]QQQQQQQQR       ATXN3  
6127                         YKSDSDNQQGSGVPSR         NaN  
6128             YKSDSDN[Deamidated]QQGSGVPSR         NaN  
6129             YKSDSDNQ[Deamidated]QGSGVPSR         NaN  

[200 rows x 4 columns]

In [82]:
df_fail_peps_no_gene_symbol = df_fail_peps[df_fail_peps["gene_symbol"].isna()]
df_fail_peps_no_gene_symbol

sequence_x protein_accessions  \
123                       AEDTAVYFCAK         GCA_294782   
359                     ANGGTTDYAAPVK          GCA_82883   
360                     ANGGTTDYAAPVK          GCA_82883   
468                   ASGYTFTNNGITWVR         GCA_197511   
469                   ASGYTYTDYYMHWVR         GCA_152779   
470                   ASGYTYTDYYMHWVR         GCA_152779   
491                ASQSISTWLAWYQQKPGK         GCA_213376   
492                ASQSISTWLAWYQQKPGK         GCA_213376   
493                ASQSISTWLAWYQQKPGK         GCA_213376   
870     DLCPLLSEHGLQCSLEPHLNSNLCVYCCK         GCA_125675   
871     DLCPLLSEHGLQCSLEPHLNSNLCVYCCK         GCA_125675   
872     DLCPLLSEHGLQCSLEPHLNSNLCVYCCK         GCA_125675   
1041                    DTSISTAYMDLSR         GCA_152779   
1591     ESGPVLVKPTETLTLTCTISGFSLSNAR         GCA_188341   
2943  KTPESFLGPNAALVDLDSLVSRPGPTLPGAK         GCA_217037   
2944  KTPESFLGPNAALVDLDSLVSRPGPTLPGAK         GCA_217037   
3052           LEEECEGREPGLETGTQAADCK         GCA_150561   
3053           LEEECEGREPGLETGTQAADCK         GCA_150561   
3054      LEEECEGREPGLETGTQAADCKDAPLK         GCA_150561   
3118                  LEWMGWINTGNGNTK         GCA_280519   
3291                        LLIFGASTR         GCA_157295   
3499              LSCAASGFTFSTYGMHWVR         GCA_294782   
3500              LSCAVSGFTFSSYAMHWVR         GCA_218596   
3874                NDNIPEQDSLGLSNLQK         GCA_121408   
3875                NDNIPEQDSLGLSNLQK         GCA_121408   
3876                NDNIPEQDSLGLSNLQK         GCA_121408   
3877                NDNIPEQDSLGLSNLQK         GCA_121408   
3878                NDNIPEQDSLGLSNLQK         GCA_121408   
4057           NQVVLTMTNMNPVDTATYYCAR         GCA_149168   
4058           NQVVLTMTNMNPVDTATYYCAR         GCA_149168   
4059           NQVVLTMTNMNPVDTATYYCAR         GCA_149168   
4060           NQVVLTMTNMNPVDTATYYCAR         GCA_149168   
4116           NTLYHQMNSLRAEDTAVYYCAR         GCA_274675   
4117           NTLYHQMNSLRAEDTAVYYCAR         GCA_274675   
4710                    SAGGGTYYADSVK         GCA_134310   
4833                  SKANGGTTDYAAPVK          GCA_82883   
4834                  SKANGGTTDYAAPVK          GCA_82883   
5065       SSPVFQIPKNDNIPEQDSLGLSNLQK         GCA_121408   
5066       SSPVFQIPKNDNIPEQDSLGLSNLQK         GCA_121408   
5067       SSPVFQIPKNDNIPEQDSLGLSNLQK         GCA_121408   
5068       SSPVFQIPKNDNIPEQDSLGLSNLQK         GCA_121408   
5069       SSPVFQIPKNDNIPEQDSLGLSNLQK         GCA_121408   
5285             TGEVVLTQSPGTLSLSPGER         GCA_262675   
5401   TPESFLGPNAALVDLDSLVSRPGPTLPGAK         GCA_217037   
5402   TPESFLGPNAALVDLDSLVSRPGPTLPGAK         GCA_217037   
5740                 VLIYGASSLQSGVPSR         GCA_161637   
5741                 VLIYGASSLQSGVPSR         GCA_161637   
6127                 YKSDSDNQQGSGVPSR         GCA_310162   
6128                 YKSDSDNQQGSGVPSR         GCA_310162   
6129                 YKSDSDNQQGSGVPSR         GCA_310162   

                                            peptidoform gene_symbol  
123                        AEDTAVYFC[Carbamidomethyl]AK         NaN  
359                                       ANGGTTDYAAPVK         NaN  
360                           AN[Deamidated]GGTTDYAAPVK         NaN  
468                                     ASGYTFTNNGITWVR         NaN  
469                                     ASGYTYTDYYMHWVR         NaN  
470                          ASGYTYTDYYM[Oxidation]HWVR         NaN  
491                                  ASQSISTWLAWYQQKPGK         NaN  
492          ASQSISTWLAWYQ[Deamidated]Q[Deamidated]KPGK         NaN  
493   ASQ[Deamidated]SISTWLAWYQ[Deamidated]Q[Deamida...         NaN  
870   DLC[Carbamidomethyl]PLLSEHGLQ[Deamidated]C[Car...         NaN  
871   DLC[Carbamidomethyl]PLLSEHGLQ[Deamidated]C[Car...         NaN  
872   DLC[Carbamidomethyl]PLLSEHGLQC[Carbamidomethyl...         NaN  
1041                                      DTSISTAYMDLSR 

In [83]:
len(set(df_fail_peps_no_gene_symbol["sequence_x"]))

25

In [84]:
auto = ahocorasick.Automaton()

for seq in fail_peps:
    auto.add_word(seq, seq)

auto.make_automaton()

In [85]:
peps_prots = {}
# for prot_file in tqdm(glob('/mnt/nfs/wangd/project/paper_db/pep_files/*.fa')):
for prot_file in tqdm(glob('F:\HPC\paper_db\pep_files\*.fa')):
    prot_seqs = set()
    prots_dict = {}
    parsed_file = SeqIO.parse(prot_file, 'fasta')
    sample_name = prot_file.split('/')[-1].split('-')[1]

    for record in parsed_file:
        try:
            prots_dict[str(record.seq)].append(sample_name + ' ' +  str(record.id) + ' ' +  str(record.seq) + ' ' + str(record.description))
        except KeyError:
            prots_dict[str(record.seq)] = [sample_name + ' ' + str(record.id) + ' ' +  str(record.seq) + ' ' + str(record.description)]
#     print('Total number of unique protein sequences = {} in the fasta file: {}'.format(len(prots_dict.keys()), prot_file))

    #get non-canonical peptides that are found in canonical proteins from ensembl
    found_prots = set()

    for prot_seq in prots_dict.keys():
        for end_ind, found in auto.iter(prot_seq):
            found_prots.add(found)
            try:
                peps_prots[found].append(prots_dict[prot_seq])
            except KeyError:
                peps_prots[found] = [prots_dict[prot_seq]]

# print('Numner of peptides found in the protein files {} and number of peptides {}'.format(len(peps_prots), len(peps)))

100%|██████████| 97/97 [04:53<00:00,  3.02s/it]


In [86]:
sample_peps= {}
gene_ID_peps = {}
protein_ID_peps = {}
protein_Seq_peps = {}
transcript_ID_peps = {}
gene_symbol_peps = {}
peps_infos = {}
res_infos = {}
for pep in tqdm(fail_peps):
    prots = [x.split(' ') for xs in peps_prots[pep] for x in xs]
    samples, proteins, proteins_seq, genes, gene_symbols, transcripts, gene_biotypes = set(), set(), set(), set(), set(), set(), set()

    for prot in prots:
        samples.add(prot[0])
        proteins.add(prot[1])
        proteins_seq.add(prot[2])
        genes.add([x for x in prot if x.startswith('gene:')][0].split(':')[-1])
        transcripts.add([x for x in prot if x.startswith('transcript:')][0].split(':')[-1])
        gene_biotypes.add([x for x in prot if x.startswith('gene_biotype:')][0].split(':')[-1])

        if res_infos.get(prot[2]):
            res_infos[prot[2]][0].add(pep)
            res_infos[prot[2]][1].add(prot[0])
        else:
            res_infos[prot[2]] = [{pep},{prot[0]},set()]

        try:
            gene_symbols.add([x for x in prot if x.startswith('gene_symbol:')][0].split(':')[-1])
            res_infos[prot[2]][2].add([x for x in prot if x.startswith('gene_symbol:')][0].split(':')[-1])
        except IndexError:
            pass

    peps_infos[pep] = [','.join(gene_symbols), ','.join(gene_biotypes), ','.join(samples), ','.join(proteins), ','.join(proteins_seq), ','.join(genes), ','.join(transcripts)]

    for sample in samples:
        try:
            sample_peps[sample].add(pep)
        except KeyError:
            sample_peps[sample] = set()
            sample_peps[sample].add(pep)

    for gene in genes:
        try:
            gene_ID_peps[gene].add(pep)
        except KeyError:
            gene_ID_peps[gene] = set()
            gene_ID_peps[gene].add(pep)

    for prot_id in proteins:
        try:
            protein_ID_peps[prot_id].add(pep)
        except KeyError:
            protein_ID_peps[prot_id] = set()
            protein_ID_peps[prot_id].add(pep)

    for prot_seq in proteins_seq:
        try:
            protein_Seq_peps[prot_seq].add(pep)
        except KeyError:
            protein_Seq_peps[prot_seq] = set()
            protein_Seq_peps[prot_seq].add(pep)

    for transcript in transcripts:
        try:
            transcript_ID_peps[transcript].add(pep)
        except KeyError:
            transcript_ID_peps[transcript] = set()
            transcript_ID_peps[transcript].add(pep)

    for gene_symbol in gene_symbols:
        try:
            gene_symbol_peps[gene_symbol].add(pep)
        except KeyError:
            gene_symbol_peps[gene_symbol] = set()
            gene_symbol_peps[gene_symbol].add(pep)

100%|██████████| 124/124 [00:00<00:00, 454.52it/s]


#### peptide_gca_proteins.tsv

In [87]:
peptide_gca_proteins = pd.DataFrame.from_dict(res_infos, orient='index')
peptide_gca_proteins.columns = ["matching_peptides","sample names","gene_symbol of matching protein"]
peptide_gca_proteins.index.name = "matching_protein_sequence"

# peptide_gca_proteins["peptides_nums"] =  peptide_gca_proteins["matching_peptides"].apply(lambda x: len(x))
# peptide_gca_proteins["sample_nums"] =  peptide_gca_proteins["sample names"].apply(lambda x: len(x))
# peptide_gca_proteins["gene_symbol of matching protein_nums"] =  peptide_gca_proteins["gene_symbol of matching protein"].apply(lambda x: len(x))
peptide_gca_proteins["matching_peptides"] =  peptide_gca_proteins["matching_peptides"].apply(lambda x: ",".join(x))
peptide_gca_proteins["sample names"] =  peptide_gca_proteins["sample names"].apply(lambda x: ",".join(x))
peptide_gca_proteins["gene_symbol of matching protein"] =  peptide_gca_proteins["gene_symbol of matching protein"].apply(lambda x: ",".join(x))

In [88]:
peptide_gca_proteins

matching_peptides  \
matching_protein_sequence                                                            
MDILCSTLLLLTVPSWVISQVTLKEAGPALVKTTQTLTLTCTFSGFS...          NQVVLTMTNMNPVDTATYYCAR   
MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVLQ...                  SDASSDQGPASPQK   
MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVLQ...                  SDASSDQGPASPQK   
MVFRRFVEVGRVAYVSFGPHAGKLVAIVDVIDQNRALVDGPCTQVRR...                GTAAAAAAAAAAAAAK   
MDSEGGSLLLDEDSEVFKMLQENREGRAAPRQSSSFRLLQEALEAEE...               SRPPGCYTCADCGLNLK   
...                                                                            ...   
MASVGRSEGTAGGGAGPEEPRREEGRAGLSPSSPPGSHSMRYFYTAM...  FDSDAASPRTEPRAPWIEQEGPEYWDGETR   
MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVIQ...                LVATSLEGKFHVFDVR   
XRNMALRWETNIKNGVCSLEFDRKDISMNKLVATSLEGKFHVFDVRT...                LVATSLEGKFHVFDVR   
MPVYSVKGHKEIINAIDGIGGLGIGEGAPEIVTGSRDGTVKVWDPRQ...                LVATSLEGKFHVFDVR   
MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVIQ...                LVATSLEGKFHVFDVR   

                                                                                         sample names  \
matching_protein_sequence                                                                               
MDILCSTLLLLTVPSWVISQVTLKEAGPALVKTTQTLTLTCTFSGFS...                                    GCA_018469865.1   
MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVLQ...    GCA_018472715.1,GCA_018471535.1,GCA_018504085.1   
MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVLQ...    GCA_018472715.1,GCA_018471535.1,GCA_018504085.1   
MVFRRFVEVGRVAYVSFGPHAGKLVAIVDVIDQNRALVDGPCTQVRR...  GCA_018471075.1,GCA_018505835.1,GCA_018471085....   
MDSEGGSLLLDEDSEVFKMLQENREGRAAPRQSSSFRLLQEALEAEE...                                    GCA_018472725.1   
...                                                                                               ...   
MASVGRSEGTAGGGAGPEEPRREEGRAGLSPSSPPGSHSMRYFYTAM...                    GCA_018503575.1,GCA_018504055.1   
MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVIQ...  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
XRNMALRWETNIKNGVCSLEFDRKDISMNKLVATSLEGKFHVFDVRT...  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
MPVYSVKGHKEIINAIDGIGGLGIGEGAPEIVTGSRDGTVKVWDPRQ...  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVIQ...  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   

                                                   gene_symbol of matching protein  
matching_protein_sequence                                                           
MDILCSTLLLLTVPSWVISQVTLKEAGPALVKTTQTLTLTCTFSGFS...                                  
MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVLQ...                        UHRF1BP1  
MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVLQ...                        UHRF1BP1  
MVFRRFVEVGRVAYVSFGPHAGKLVAIVDVIDQNRALVDGPCTQVRR...                           RPL14  
MDSEGGSLLLDEDSEVFKMLQENREGRAAPRQSSSFRLLQEALEAEE...                          PDLIM2  
...                                                                            ...  
MASVGRSEGTAGGGAGPEEPRREEGRAGLSPSSPPGSHSMRYFYTAM...                           HLA-B  
MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVIQ...                           WDR92  
XRNMALRWETNIKNGVCSLEFDRKDISMNKLVATSLEGKFHVFDVRT...                           WDR92  
MPVYSVKGHKEIINAIDGIGGLGIGEGAPEIVTGSRDGTVKVWDPRQ...                           WDR92  
MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVIQ...                           WDR92  

[800 rows x 3 columns]

In [89]:
peptide_gca_proteins.to_csv(r"F:\HPC\paper_db\count\blast_canonical_count\peptide_gca_proteins.tsv", header=1, sep="\t")

#### matching_gca_canoical_proteins.tsv

In [90]:
matching_gca_canoical_proteins = pd.read_table(r"F:\HPC\paper_db\count\blast_canonical_count\peptide_gca_proteins.tsv")

In [91]:
matching_gca_canoical_proteins

matching_protein_sequence  \
0    MDILCSTLLLLTVPSWVISQVTLKEAGPALVKTTQTLTLTCTFSGF...   
1    MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVL...   
2    MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVL...   
3    MVFRRFVEVGRVAYVSFGPHAGKLVAIVDVIDQNRALVDGPCTQVR...   
4    MDSEGGSLLLDEDSEVFKMLQENREGRAAPRQSSSFRLLQEALEAE...   
..                                                 ...   
795  MASVGRSEGTAGGGAGPEEPRREEGRAGLSPSSPPGSHSMRYFYTA...   
796  MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVI...   
797  XRNMALRWETNIKNGVCSLEFDRKDISMNKLVATSLEGKFHVFDVR...   
798  MPVYSVKGHKEIINAIDGIGGLGIGEGAPEIVTGSRDGTVKVWDPR...   
799  MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVI...   

                  matching_peptides  \
0            NQVVLTMTNMNPVDTATYYCAR   
1                    SDASSDQGPASPQK   
2                    SDASSDQGPASPQK   
3                  GTAAAAAAAAAAAAAK   
4                 SRPPGCYTCADCGLNLK   
..                              ...   
795  FDSDAASPRTEPRAPWIEQEGPEYWDGETR   
796                LVATSLEGKFHVFDVR   
797                LVATSLEGKFHVFDVR   
798                LVATSLEGKFHVFDVR   
799                LVATSLEGKFHVFDVR   

                                          sample names  \
0                                      GCA_018469865.1   
1      GCA_018472715.1,GCA_018471535.1,GCA_018504085.1   
2      GCA_018472715.1,GCA_018471535.1,GCA_018504085.1   
3    GCA_018471075.1,GCA_018505835.1,GCA_018471085....   
4                                      GCA_018472725.1   
..                                                 ...   
795                    GCA_018503575.1,GCA_018504055.1   
796  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
797  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
798  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
799  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   

    gene_symbol of matching protein  
0                               NaN  
1                          UHRF1BP1  
2                          UHRF1BP1  
3                             RPL14  
4                            PDLIM2  
..                              ...  
795                           HLA-B  
796                           WDR92  
797                           WDR92  
798                           WDR92  
799                           WDR92  

[800 rows x 4 columns]

In [92]:
def get_blast_canonical_info(x):
    blast_res = {}
    non_canonical_seq = x["matching_protein_sequence"]

    if gene_symbol_proteins.get(x["gene_symbol of matching protein"]):
        canonical_seqs = gene_symbol_proteins[x["gene_symbol of matching protein"]]

        for canonical_seq in canonical_seqs:
            seq = canonical_seq.split(";")[0]
            alignments = pairwise2.align.globalms(sequenceA = seq,sequenceB = non_canonical_seq, match = 1,mismatch = -1,open = -2,extend = -1,one_alignment_only=True)
            alignment = alignments[0]
            score = alignment.score
            if blast_res:
                for value in blast_res.values():
                    if value.score > score:
                        continue
                    elif value == score:
                        blast_res[canonical_seq] = alignment
                    else:
                        blast_res = {canonical_seq:alignment}
            else:
                blast_res = {canonical_seq:alignment}

        final_res = []
        for key,value in blast_res.items():
            res = []
            i = 0
            j = 0
            for AA1, AA2 in zip(value.seqA, value.seqB):
                i += 1
                j += 1
                if AA1 == AA2:
                    continue
                if AA1 == '-' and AA2 != '-':
                    # insertion
                    res.append(str(i) + "-" + ">" + AA2)
                    i -= 1
                elif AA2 == '-' and AA1 != '-':
                    # deletion
                    res.append(str(i) + AA1 + ">" + "-")
                    j -= 1
                else:
                    # substitution
                    res.append(str(i) + AA1 + ">" + AA2)

            final_res.append({key:res})

        return final_res
    else:
        return ""

In [93]:
tqdm.pandas()
matching_gca_canoical_proteins["match_info"] = matching_gca_canoical_proteins.progress_apply( get_blast_canonical_info,axis=1)

100%|██████████| 800/800 [17:51<00:00,  1.34s/it]


In [94]:
matching_gca_canoical_proteins

matching_protein_sequence  \
0    MDILCSTLLLLTVPSWVISQVTLKEAGPALVKTTQTLTLTCTFSGF...   
1    MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVL...   
2    MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVL...   
3    MVFRRFVEVGRVAYVSFGPHAGKLVAIVDVIDQNRALVDGPCTQVR...   
4    MDSEGGSLLLDEDSEVFKMLQENREGRAAPRQSSSFRLLQEALEAE...   
..                                                 ...   
795  MASVGRSEGTAGGGAGPEEPRREEGRAGLSPSSPPGSHSMRYFYTA...   
796  MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVI...   
797  XRNMALRWETNIKNGVCSLEFDRKDISMNKLVATSLEGKFHVFDVR...   
798  MPVYSVKGHKEIINAIDGIGGLGIGEGAPEIVTGSRDGTVKVWDPR...   
799  MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVI...   

                  matching_peptides  \
0            NQVVLTMTNMNPVDTATYYCAR   
1                    SDASSDQGPASPQK   
2                    SDASSDQGPASPQK   
3                  GTAAAAAAAAAAAAAK   
4                 SRPPGCYTCADCGLNLK   
..                              ...   
795  FDSDAASPRTEPRAPWIEQEGPEYWDGETR   
796                LVATSLEGKFHVFDVR   
797                LVATSLEGKFHVFDVR   
798                LVATSLEGKFHVFDVR   
799                LVATSLEGKFHVFDVR   

                                          sample names  \
0                                      GCA_018469865.1   
1      GCA_018472715.1,GCA_018471535.1,GCA_018504085.1   
2      GCA_018472715.1,GCA_018471535.1,GCA_018504085.1   
3    GCA_018471075.1,GCA_018505835.1,GCA_018471085....   
4                                      GCA_018472725.1   
..                                                 ...   
795                    GCA_018503575.1,GCA_018504055.1   
796  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
797  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
798  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
799  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   

    gene_symbol of matching protein  \
0                               NaN   
1                          UHRF1BP1   
2                          UHRF1BP1   
3                             RPL14   
4                            PDLIM2   
..                              ...   
795                           HLA-B   
796                           WDR92   
797                           WDR92   
798                           WDR92   
799                           WDR92   

                                            match_info  
0                                                       
1                                                       
2                                                       
3    [{'MVFRRFVEVGRVAYVSFGPHAGKLVAIVDVIDQNRALVDGPCT...  
4    [{'MDSEGGSLLLDEDSEVFKMLQENREGRAAPRQSSSFRLLQEAL...  
..                                                 ...  
795  [{'MASVGRREGTAGGGAGPGEPRREEGRAGLSPSSPPGSHSMRYF...  
796                                                     
797                                                     
798                                                     
799                                                     

[800 rows x 5 columns]

In [95]:
matching_gca_canoical_proteins = matching_gca_canoical_proteins.explode("match_info", ignore_index=True)

In [96]:
matching_gca_canoical_proteins

matching_protein_sequence  \
0    MDILCSTLLLLTVPSWVISQVTLKEAGPALVKTTQTLTLTCTFSGF...   
1    MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVL...   
2    MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVL...   
3    MVFRRFVEVGRVAYVSFGPHAGKLVAIVDVIDQNRALVDGPCTQVR...   
4    MDSEGGSLLLDEDSEVFKMLQENREGRAAPRQSSSFRLLQEALEAE...   
..                                                 ...   
795  MASVGRSEGTAGGGAGPEEPRREEGRAGLSPSSPPGSHSMRYFYTA...   
796  MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVI...   
797  XRNMALRWETNIKNGVCSLEFDRKDISMNKLVATSLEGKFHVFDVR...   
798  MPVYSVKGHKEIINAIDGIGGLGIGEGAPEIVTGSRDGTVKVWDPR...   
799  MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVI...   

                  matching_peptides  \
0            NQVVLTMTNMNPVDTATYYCAR   
1                    SDASSDQGPASPQK   
2                    SDASSDQGPASPQK   
3                  GTAAAAAAAAAAAAAK   
4                 SRPPGCYTCADCGLNLK   
..                              ...   
795  FDSDAASPRTEPRAPWIEQEGPEYWDGETR   
796                LVATSLEGKFHVFDVR   
797                LVATSLEGKFHVFDVR   
798                LVATSLEGKFHVFDVR   
799                LVATSLEGKFHVFDVR   

                                          sample names  \
0                                      GCA_018469865.1   
1      GCA_018472715.1,GCA_018471535.1,GCA_018504085.1   
2      GCA_018472715.1,GCA_018471535.1,GCA_018504085.1   
3    GCA_018471075.1,GCA_018505835.1,GCA_018471085....   
4                                      GCA_018472725.1   
..                                                 ...   
795                    GCA_018503575.1,GCA_018504055.1   
796  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
797  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
798  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
799  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   

    gene_symbol of matching protein  \
0                               NaN   
1                          UHRF1BP1   
2                          UHRF1BP1   
3                             RPL14   
4                            PDLIM2   
..                              ...   
795                           HLA-B   
796                           WDR92   
797                           WDR92   
798                           WDR92   
799                           WDR92   

                                            match_info  
0                                                       
1                                                       
2                                                       
3    {'MVFRRFVEVGRVAYVSFGPHAGKLVAIVDVIDQNRALVDGPCTQ...  
4    {'MDSEGGSLLLDEDSEVFKMLQENREGRAAPRQSSSFRLLQEALE...  
..                                                 ...  
795  {'MASVGRREGTAGGGAGPGEPRREEGRAGLSPSSPPGSHSMRYFY...  
796                                                     
797                                                     
798                                                     
799                                                     

[800 rows x 5 columns]

In [97]:
matching_gca_canoical_proteins["canonical_protein_seq"] = matching_gca_canoical_proteins["match_info"].apply(lambda x: list(x.keys())[0].split(";")[0] if x and list(x.keys())[0] != "" else None)
matching_gca_canoical_proteins["number_mismatches"] = matching_gca_canoical_proteins["match_info"].apply(lambda x: len(list(x.values())[0]) if x and list(x.values())[0] != "" else None)
matching_gca_canoical_proteins["mismatch_info"] = matching_gca_canoical_proteins["match_info"].apply(lambda x: ",".join(list(x.values())[0]) if x and list(x.values())[0] != "" else None)
matching_gca_canoical_proteins["canonical_protein_ID"] = matching_gca_canoical_proteins["match_info"].apply(lambda x: list(x.keys())[0].split(";")[1].split(" ")[0] if x and list(x.keys())[0] != "" else None)
matching_gca_canoical_proteins["canonical_transcript_ID"] = matching_gca_canoical_proteins["match_info"].apply(lambda x: [x for x in list(x.keys())[0].split(" ") if x.startswith('transcript:')][0].split(':')[-1] if x and list(x.keys())[0] != "" else None)

In [98]:
matching_gca_canoical_proteins = matching_gca_canoical_proteins.drop("match_info", axis=1)

In [99]:
matching_gca_canoical_proteins

matching_protein_sequence  \
0    MDILCSTLLLLTVPSWVISQVTLKEAGPALVKTTQTLTLTCTFSGF...   
1    MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVL...   
2    MAGIIKKQILKHLSRFTKNLSPDKINLSTLKGEGQLTNLELDEEVL...   
3    MVFRRFVEVGRVAYVSFGPHAGKLVAIVDVIDQNRALVDGPCTQVR...   
4    MDSEGGSLLLDEDSEVFKMLQENREGRAAPRQSSSFRLLQEALEAE...   
..                                                 ...   
795  MASVGRSEGTAGGGAGPEEPRREEGRAGLSPSSPPGSHSMRYFYTA...   
796  MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVI...   
797  XRNMALRWETNIKNGVCSLEFDRKDISMNKLVATSLEGKFHVFDVR...   
798  MPVYSVKGHKEIINAIDGIGGLGIGEGAPEIVTGSRDGTVKVWDPR...   
799  MSAFEKPQIIAHIQKGFNYTVFDCKWVPCSAKFVTMGNFARGTGVI...   

                  matching_peptides  \
0            NQVVLTMTNMNPVDTATYYCAR   
1                    SDASSDQGPASPQK   
2                    SDASSDQGPASPQK   
3                  GTAAAAAAAAAAAAAK   
4                 SRPPGCYTCADCGLNLK   
..                              ...   
795  FDSDAASPRTEPRAPWIEQEGPEYWDGETR   
796                LVATSLEGKFHVFDVR   
797                LVATSLEGKFHVFDVR   
798                LVATSLEGKFHVFDVR   
799                LVATSLEGKFHVFDVR   

                                          sample names  \
0                                      GCA_018469865.1   
1      GCA_018472715.1,GCA_018471535.1,GCA_018504085.1   
2      GCA_018472715.1,GCA_018471535.1,GCA_018504085.1   
3    GCA_018471075.1,GCA_018505835.1,GCA_018471085....   
4                                      GCA_018472725.1   
..                                                 ...   
795                    GCA_018503575.1,GCA_018504055.1   
796  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
797  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
798  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   
799  GCA_018503525.1,GCA_018504075.1,GCA_018503265....   

    gene_symbol of matching protein  \
0                               NaN   
1                          UHRF1BP1   
2                          UHRF1BP1   
3                             RPL14   
4                            PDLIM2   
..                              ...   
795                           HLA-B   
796                           WDR92   
797                           WDR92   
798                           WDR92   
799                           WDR92   

                                 canonical_protein_seq  number_mismatches  \
0                                                 None                NaN   
1                                                 None                NaN   
2                                                 None                NaN   
3    MVFRRFVEVGRVAYVSFGPHAGKLVAIVDVIDQNRALVDGPCTQVR...                3.0   
4    MDSEGGSLLLDEDSEVFKMLQENREGRAAPRQSSSFRLLQEALEAE...                2.0   
..                                                 ...                ...   
795  MASVGRREGTAGGGAGPGEPRREEGRAGLSPSSPPGSHSMRYFYTA...               20.0   
796                                               None                NaN   
797                                               None                NaN   
798                                               None                NaN   
799                                               None                NaN   

                                         mismatch_info canonical_protein_ID  \
0                                                 None                 None   
1                                                 None                 None   
2                                                 None                 None   
3                                 150->A,150->A,150->A    ENSP00000379506.2   
4                                         99Y>S,101H>P    ENSP00000477546.1   
..                                                 ...                  ...   
795  7R>S,18G>E,59T>A,67L>Q,76T>A,80K>T,97R>G,100Q>...    ENSP00000416672.1   
796                                               None                 None   
797                                               None       

In [100]:
matching_gca_canoical_proteins.to_csv(r"F:\HPC\paper_db\count\blast_canonical_count\matching_gca_canoical_proteins.tsv", header=1, sep="\t",index = None)

#### Novel Peptides Info Count

In [101]:
print("Number of peptides: {}".format(len(fail_peps)))
print("Number of GCA samples matched: {}".format(len(sample_peps)))
print("Number of gene ids matched: {}".format(len(gene_ID_peps)))
print("Number of transcript ids matched: {}".format(len(transcript_ID_peps)))
print("Number of protein ids matched: {}".format(len(protein_ID_peps)))
print("Number of protein seqs matched: {}".format(len(protein_Seq_peps)))
print("Number of gene_symbols matched: {}".format(len(gene_symbol_peps)))

Number of peptides: 124
Number of GCA samples matched: 97
Number of gene ids matched: 1794
Number of transcript ids matched: 4621
Number of protein ids matched: 4621
Number of protein seqs matched: 800
Number of gene_symbols matched: 71


#### Protein_with_two_peptides

In [102]:
protein_with_two_peptides = {}
for protein_seq, peptide_seqs in protein_Seq_peps.items():
    if len(peptide_seqs) > 1:
        protein_with_two_peptides[protein_seq] = ",".join(peptide_seqs)

In [103]:
len(protein_with_two_peptides)

123

In [104]:
df_protein_with_two_peptides = pd.DataFrame(list(protein_with_two_peptides.items()), columns=['protein_seq', 'peptides'])

In [105]:
df_protein_with_two_peptides.to_csv(r"F:\HPC\paper_db\count\blast_canonical_count\protein_with_two_peptides.tsv", header=1, sep="\t",index = None)

In [106]:
df_protein_with_two_peptides

protein_seq  \
0    MKLLTGLVFCSLVLGVSSRSFFSFLGEAFDGARDMWRAYSDMREAN...   
1    MKLLTGLVFCSLVLGVSSRSFFSFLGEAFDGARDMWRAYSDMREAN...   
2    MKLLTGLVFCSLVLGVSSRSFFSFLGEAFDGARDMWRAYSDMREAN...   
3    MKLLTGLVFCSLVLGVSSRSFFSFLGEAFDGARDMWRAYSDMREAN...   
4    MGCHSSKSTTVAAESQKLEEECEGREPGLETGTQAADCKDAPLKDG...   
..                                                 ...   
118  VTGSGHASSTPGGEKETSATQRSSVPSSTEKNAVSMTSSVLSSHSP...   
119  MTPGTQSPFFLLLLLTVLTVVTGSGHASSTPGGEKETSATQRSSVP...   
120  MVFRRFVEVGRVAYVSFGPHAGKLVAIVDVIDQNRALVDGPCTQVR...   
121  AILKGVQCEVQLVESAGGLVQPGGSLRLSCAASGFTCSNAWMSWVR...   
122  AILKGVQCEVQLVESAGGLVQPGGSLRLSCAASGFTCSNAWMSWVR...   

                                              peptides  
0    GPGGVWAAEAISDARENIQR,RGPGGVWAAEAISDARENIQR,GNY...  
1    GPGGVWAAEAISDARENIQR,RGPGGVWAAEAISDARENIQR,GNY...  
2    GPGGVWAAEAISDARENIQR,RGPGGVWAAEAISDARENIQR,GNY...  
3    GPGGVWAAEAISDARENIQR,RGPGGVWAAEAISDARENIQR,GNY...  
4    LEEECEGREPGLETGTQAADCK,LEEECEGREPGLETGTQAADCKD...  
..                                                 ...  
118          PAPGSTAPAAHGVTSAPESR,PAPGSTAPPAHGVTSAPESR  
119          PAPGSTAPAAHGVTSAPESR,PAPGSTAPPAHGVTSAPESR  
120              GTAAAAAAAAAAAAK,KAPGTKGTAAAAAAAAAAAAK  
121                      SKANGGTTDYAAPVK,ANGGTTDYAAPVK  
122                      SKANGGTTDYAAPVK,ANGGTTDYAAPVK  

[123 rows x 2 columns]